<a href="https://colab.research.google.com/github/vikrantkumar256/Exploratory-Project/blob/master/hinditransfer.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [37]:
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Mounted at /content/drive


In [0]:
import os
import sys
import bs4 
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import Embedding,GRU,Dense,Conv2D,MaxPool2D,Input,Dropout,Activation,Bidirectional,Concatenate,Lambda,Reshape,Conv1D,MaxPooling1D
from tensorflow.keras.utils import to_categorical
import tensorflow.keras.backend as K

In [0]:
disease_f = os.listdir('/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data')
tourism_f = os.listdir('/content/drive/My Drive/Hindi-domain-treebank/Hindi-Tourism/Data')

In [40]:
print(disease_f)
print(tourism_f)

['mor-पोलियो-pos-chunk-1-50-posn-name', 'mor-डेंगू-pos-chunk-151-200-posn-name', 'mor-धूम्रपान-pos-chunk-101-150-posn-name', 'mor-निमोनिया-pos-chunk-101-150-posn-name', 'mor-खसरा-pos-chunk-101-124-posn-name', 'mor-डिप्थीरिया-pos-chunk-1-50-posn-name', 'mor-निमोनिया-pos-chunk-1-50-posn-name', 'mor-खसरा-pos-chunk-51-100-posn-name', 'mor-डेंगू-pos-chunk-101-150-posn-name', 'mor-डेंगू-pos-chunk-201-250-posn-name', 'mor-तपेदिक-pos-chunk-351-400-posn-name', 'mor-निमोनिया-pos-chunk-201-237-posn-name', 'mor-इनफ्लुएंजा-pos-chunk-1-50-posn-name', 'mor-निमोनिया-pos-chunk-151-200-posn-name', 'mor-तपेदिक-pos-chunk-101-150-posn-name', 'mor-इनफ्लुएंजा-pos-chunk-51-69-posn-name', 'mor-पोलियो-pos-chunk-51-102-posn-name', 'mor-ऑस्टियोपोरोसिस-pos-chunk-101-150-posn-name', 'mor-तपेदिक-pos-chunk-401-422-posn-name', 'mor-डेंगू-pos-chunk-251-270-posn-name', 'mor-डेंगू-pos-chunk-51-100-posn-name', 'mor-मलेरिया-1-50-posn-name', 'mor-निमोनिया-pos-chunk-51-100-posn-name', 'mor-पार्किंसन-pos-chunk-51-74-posn-name

In [0]:
disease_ff = ["/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/" + x for x in disease_f]
tourism_ff = ["/content/drive/My Drive/Hindi-domain-treebank/Hindi-Tourism/Data/" + x for x in tourism_f]

In [42]:
print(disease_ff)
print(tourism_ff)

['/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-पोलियो-pos-chunk-1-50-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-डेंगू-pos-chunk-151-200-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-धूम्रपान-pos-chunk-101-150-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-निमोनिया-pos-chunk-101-150-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-खसरा-pos-chunk-101-124-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-डिप्थीरिया-pos-chunk-1-50-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-निमोनिया-pos-chunk-1-50-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-खसरा-pos-chunk-51-100-posn-name', '/content/drive/My Drive/Hindi-domain-treebank/Hindi-Diseases/Data/mor-डेंगू-pos-chunk-101-150-posn-name', '/content/drive/My Drive/Hindi-do

In [0]:
def part_preprocess(fileName,dis_feature_data,dis_label_data):
  f = open(fileName,'r').read()
  soup = bs4.BeautifulSoup(f)
  all_sentence = soup.find_all('sentence')
  for j in range(len(all_sentence)):
    sing = all_sentence[j]
    feature_post_elem = []
    label_post_elem = []
    z = (sing.get_text()).replace("\t"," ").split("))")
    for i in range(len(z)):
      part_sent = (z[i].split("\n"))
      for x in part_sent:
        if(x!="" and x!=" "):
          a = x.split(" ")
          if(a[2]!=""):
            feature_post_elem.append(a[1])
            label_post_elem.append(a[2])
            
    dis_feature_data.append(feature_post_elem)
    dis_label_data.append(label_post_elem)



In [0]:
dis_feature_data = []
dis_label_data = []
for i in range(len(disease_ff)):
  part_preprocess(disease_ff[i],dis_feature_data,dis_label_data)

In [45]:
print(len(dis_feature_data))
print(len(dis_label_data))

1494
1494


In [0]:
tour_feature_data = []
tour_label_data = []
for i in range(len(tourism_ff)):
  part_preprocess(tourism_ff[i],tour_feature_data,tour_label_data)


In [47]:
print(len(tour_feature_data))
print(len(tour_label_data))
print(tour_feature_data)
print(tour_label_data)

3022
3022
[['((', 'आमेर', 'का', '((', 'प्रसिद्ध', 'दुर्ग', '((', 'आज', 'भी', '((', 'ऐतिहासिक', 'फिल्मों', 'के', '((', 'निर्माताओं', 'को', '((', 'शूटिंग', 'के', 'लिए', '((', 'आमंत्रित', '((', 'करता', 'है', '((', '।'], ['((', 'दुर्ग', 'का', '((', 'मुख्य', 'द्वार', '((', 'गणेश', 'पोल', '((', 'कहलाता', 'है', '((', '।'], ['((', 'मुख्य', 'द्वार', 'की', '((', 'नक्काशी', '((', 'अत्यन्त', 'आकर्षक', '((', 'है', '((', '।'], ['((', 'आमेर', 'में', 'ही', '((', 'है', '((', 'चालीस', 'खम्बों', 'वाला', '((', 'वह', 'शीश', 'महल', ',', '((', 'जहाँ', '((', 'माचिस', 'की', '((', 'तीली', '((', 'जलाने', 'पर', '((', 'सारे', 'महल', 'में', '((', 'दीपावलियाँ', '((', 'आलोकित', '((', 'हो', 'उठती', 'है', '((', '।'], ['((', 'हाथी', 'की', '((', 'सवारी', '((', 'यहाँ', 'का', '((', 'विशेष', 'आकर्षण', '((', 'है', '((', '।'], ['((', 'जो', '((', 'देशी', 'सैलानियों', 'से', '((', 'अधिक', '((', 'विदेशी', 'पर्यटकों', 'के', 'लिए', '((', 'कौतूहल', '((', 'और', '((', 'आनंद', 'का', '((', 'विषय', '((', 'है', '((', '।'], ['((', 'सतपुड़ा

In [0]:
def pos_tag_separater(listName,listName1):
  pos_data = []
  pos_label = []
  for i in range(len(listName)):
    pos_elem_lst = []
    pos_label_lst = []
    for j in range(len(listName[i])):
      if(listName[i][j] != "(("):
        pos_elem_lst.append(listName[i][j])
        pos_label_lst.append(listName1[i][j])
    pos_data.append(pos_elem_lst)
    pos_label.append(pos_label_lst)
  return (pos_data,pos_label)


In [0]:
def chunk_tag_separater(listName,listName1):
  chunk_data = []
  chunk_label = []
  for i in range(len(listName)):
    chunk_elem_lst = []
    chunk_label_lst = []
    chunk = listName1[i][0]
    for j in range(len(listName[i])):
      if(listName[i][j] == "(("):
        chunk = listName1[i][j]
      else:
        chunk_elem_lst.append(listName[i][j])
        chunk_label_lst.append(chunk)
    chunk_data.append(chunk_elem_lst)
    chunk_label.append(chunk_label_lst)
  return (chunk_data,chunk_label)
        


In [0]:
chunk_feature_dis,chunk_label_dis = chunk_tag_separater(dis_feature_data,dis_label_data)

In [151]:
print(dis_feature_data)
print(dis_label_data)

[['((', 'पोलियो', 'वैक्सीन'], ['((', 'दुनियाभर', 'में', '((', 'पोलिओम्येलितिस', '((', '(', 'या', '((', 'पोलिओ', ')', '((', 'का', '((', 'मुकाबला', '((', 'करने', 'के', 'लिए', '((', 'दो', 'पोलियो', 'वैक्सीन', 'का', '((', 'प्रयोग', '((', 'किया', 'जाता', 'है', '((', '।'], ['((', 'पहला', '((', 'जोनास', 'सॉल्क', 'द्वारा', '((', 'विकसित', '((', 'किया', 'गया', '((', 'और', '((', '1952', 'में', '((', 'उसका', '((', 'पहला', 'परीक्षण', '((', 'किया', 'गया', '((', '।'], ['((', '1955', ',', '((', 'अप्रैल', '12', 'को', '((', 'सॉल्क', 'द्वारा', '((', 'दुनिया', 'को', '((', 'इसकी', '((', 'घोषणा', '((', 'की', 'गयी', '((', 'कि', ',', '((', 'यह', '((', 'निष्क्रिय', '((', '(', 'मरे', 'हुए', ')', '((', 'पोलियो', 'वायरस', 'के', '((', 'इंजेक्शन', 'की', '((', 'खुराक', '((', 'होते', 'हैं', '((', '।'], ['((', 'एक', 'मौखिक', 'टीका', '((', 'अल्बर्ट', 'साबिन', 'द्वारा', '((', 'तनु', '((', '(', 'कमजोर', '((', 'किये', 'गए', ')', '((', 'पोलियो', 'वायरस', 'का', '((', 'उपयोग', '((', 'करके', '((', 'विकसित', '((', 'किया', 'गय

In [152]:
print(chunk_feature_dis)
print(chunk_label_dis)

[['पोलियो', 'वैक्सीन'], ['दुनियाभर', 'में', 'पोलिओम्येलितिस', '(', 'या', 'पोलिओ', ')', 'का', 'मुकाबला', 'करने', 'के', 'लिए', 'दो', 'पोलियो', 'वैक्सीन', 'का', 'प्रयोग', 'किया', 'जाता', 'है', '।'], ['पहला', 'जोनास', 'सॉल्क', 'द्वारा', 'विकसित', 'किया', 'गया', 'और', '1952', 'में', 'उसका', 'पहला', 'परीक्षण', 'किया', 'गया', '।'], ['1955', ',', 'अप्रैल', '12', 'को', 'सॉल्क', 'द्वारा', 'दुनिया', 'को', 'इसकी', 'घोषणा', 'की', 'गयी', 'कि', ',', 'यह', 'निष्क्रिय', '(', 'मरे', 'हुए', ')', 'पोलियो', 'वायरस', 'के', 'इंजेक्शन', 'की', 'खुराक', 'होते', 'हैं', '।'], ['एक', 'मौखिक', 'टीका', 'अल्बर्ट', 'साबिन', 'द्वारा', 'तनु', '(', 'कमजोर', 'किये', 'गए', ')', 'पोलियो', 'वायरस', 'का', 'उपयोग', 'करके', 'विकसित', 'किया', 'गया', '।'], ['साबिन', 'के', 'टीके', 'का', 'मानव', 'परीक्षण', '१९५७', 'में', 'शुरू', 'किया', 'गया', 'और', 'इसने', '१९६२', 'में', 'लाइसेंस', 'प्राप्त', 'किया', '।'], ['चूँकि', 'साधारणतः', 'असंक्राम्य', 'व्यक्तियों', 'में', 'पोलिओ', 'वायरस', 'की', 'कोई', 'दीर्घकालिक', 'वाहक', 'परिस्थिति', 'नह

In [0]:
pos_feature_dis , pos_label_dis = pos_tag_separater(dis_feature_data,dis_label_data)
pos_feature_tour , pos_label_tour = pos_tag_separater(tour_feature_data,tour_label_data)

In [0]:
def char_featurizer(pos_feature_dis):
  char_feature = []
  for i in range(len(pos_feature_dis)):
    for j in range(len(pos_feature_dis[i])):
      char_feature.append(list(pos_feature_dis[i][j]))
  return char_feature


In [51]:
print(pos_feature_dis)
print(pos_label_dis)

[['पोलियो', 'वैक्सीन'], ['दुनियाभर', 'में', 'पोलिओम्येलितिस', '(', 'या', 'पोलिओ', ')', 'का', 'मुकाबला', 'करने', 'के', 'लिए', 'दो', 'पोलियो', 'वैक्सीन', 'का', 'प्रयोग', 'किया', 'जाता', 'है', '।'], ['पहला', 'जोनास', 'सॉल्क', 'द्वारा', 'विकसित', 'किया', 'गया', 'और', '1952', 'में', 'उसका', 'पहला', 'परीक्षण', 'किया', 'गया', '।'], ['1955', ',', 'अप्रैल', '12', 'को', 'सॉल्क', 'द्वारा', 'दुनिया', 'को', 'इसकी', 'घोषणा', 'की', 'गयी', 'कि', ',', 'यह', 'निष्क्रिय', '(', 'मरे', 'हुए', ')', 'पोलियो', 'वायरस', 'के', 'इंजेक्शन', 'की', 'खुराक', 'होते', 'हैं', '।'], ['एक', 'मौखिक', 'टीका', 'अल्बर्ट', 'साबिन', 'द्वारा', 'तनु', '(', 'कमजोर', 'किये', 'गए', ')', 'पोलियो', 'वायरस', 'का', 'उपयोग', 'करके', 'विकसित', 'किया', 'गया', '।'], ['साबिन', 'के', 'टीके', 'का', 'मानव', 'परीक्षण', '१९५७', 'में', 'शुरू', 'किया', 'गया', 'और', 'इसने', '१९६२', 'में', 'लाइसेंस', 'प्राप्त', 'किया', '।'], ['चूँकि', 'साधारणतः', 'असंक्राम्य', 'व्यक्तियों', 'में', 'पोलिओ', 'वायरस', 'की', 'कोई', 'दीर्घकालिक', 'वाहक', 'परिस्थिति', 'नह

In [0]:
char_pos_feature_dis = char_featurizer(pos_feature_dis)
char_pos_feature_tour = char_featurizer(pos_feature_tour)

In [53]:
print(len(char_pos_feature_dis))
print(len(char_pos_feature_tour))
print(char_pos_feature_dis)
print(char_pos_feature_tour)


36777
50126
[['प', 'ो', 'ल', 'ि', 'य', 'ो'], ['व', 'ै', 'क', '्', 'स', 'ी', 'न'], ['द', 'ु', 'न', 'ि', 'य', 'ा', 'भ', 'र'], ['म', 'े', 'ं'], ['प', 'ो', 'ल', 'ि', 'ओ', 'म', '्', 'य', 'े', 'ल', 'ि', 'त', 'ि', 'स'], ['('], ['य', 'ा'], ['प', 'ो', 'ल', 'ि', 'ओ'], [')'], ['क', 'ा'], ['म', 'ु', 'क', 'ा', 'ब', 'ल', 'ा'], ['क', 'र', 'न', 'े'], ['क', 'े'], ['ल', 'ि', 'ए'], ['द', 'ो'], ['प', 'ो', 'ल', 'ि', 'य', 'ो'], ['व', 'ै', 'क', '्', 'स', 'ी', 'न'], ['क', 'ा'], ['प', '्', 'र', 'य', 'ो', 'ग'], ['क', 'ि', 'य', 'ा'], ['ज', 'ा', 'त', 'ा'], ['ह', 'ै'], ['।'], ['प', 'ह', 'ल', 'ा'], ['ज', 'ो', 'न', 'ा', 'स'], ['स', 'ॉ', 'ल', '्', 'क'], ['द', '्', 'व', 'ा', 'र', 'ा'], ['व', 'ि', 'क', 'स', 'ि', 'त'], ['क', 'ि', 'य', 'ा'], ['ग', 'य', 'ा'], ['औ', 'र'], ['1', '9', '5', '2'], ['म', 'े', 'ं'], ['उ', 'स', 'क', 'ा'], ['प', 'ह', 'ल', 'ा'], ['प', 'र', 'ी', 'क', '्', 'ष', 'ण'], ['क', 'ि', 'य', 'ा'], ['ग', 'य', 'ा'], ['।'], ['1', '9', '5', '5'], [','], ['अ', 'प', '्', 'र', 'ै', 'ल'], ['1', '2'], ['क', 'ो'], ['स'

## Model Without Transfer Learning 
**PosTagging model on hindi disease data**
# Preprocessed data

1.   pos_feature_dis
2.   pos_label_dis
3.   pos_feature_tour
4.   pos_label_tour
5.   char_pos_feature_dis
6.   char_pos_feature_tour



In [0]:
char_tokenizer = Tokenizer(oov_token="<OOV>")
char_tokenizer.fit_on_texts(char_pos_feature_dis)
char_index = char_tokenizer.word_index

In [55]:
CHAR_MAX_LENGTH = len(max(char_pos_feature_dis,key=len))
CHAR_MAX_LENGTH

22

In [0]:
word_tokenizer = Tokenizer(oov_token="<OOV>")
word_tokenizer.fit_on_texts(pos_feature_dis)
word_index = word_tokenizer.word_index
train_word_sequences = word_tokenizer.texts_to_sequences(pos_feature_dis)
padded_word_sequences_dis = pad_sequences(train_word_sequences,padding='post',maxlen=52,truncating="post")

In [115]:
print(pos_label_dis)

[['N_NNP', 'N_NN'], ['N_NN', 'PSP', 'N_NNP', 'RD_SYM', 'CC_CCD', 'N_NNP', 'RD_SYM', 'PSP', 'N_NN', 'V_VM', 'PSP', 'PSP', 'QT_QTC', 'N_NNP', 'N_NN', 'PSP', 'N_NN', 'V_VM', 'V_VAUX', 'V_VAUX', 'RD_PUNC'], ['QT_QTO', 'N_NNP', 'N_NNP', 'PSP', 'JJ', 'V_VM', 'V_VAUX', 'CC_CCD', 'N_NNP', 'PSP', 'PR_PRP', 'QT_QTO', 'N_NN', 'V_VM', 'V_VAUX', 'RD_PUNC'], ['N_NNP', 'RD_PUNC', 'N_NNP', 'QT_QTC', 'PSP', 'N_NNP', 'PSP', 'N_NN', 'PSP', 'PR_PRP', 'N_NN', 'V_VM', 'V_VAUX', 'CC_CCS', 'RD_PUNC', 'PR_PRP', 'JJ', 'RD_SYM', 'V_VM', 'V_VAUX', 'RD_SYM', 'N_NNP', 'N_NN', 'PSP', 'N_NN', 'PSP', 'N_NN', 'V_VM', 'V_VAUX', 'RD_PUNC'], ['QT_QTC', 'JJ', 'N_NN', 'N_NNP', 'N_NNP', 'PSP', 'JJ', 'RD_SYM', 'JJ', 'V_VM', 'V_VAUX', 'RD_SYM', 'N_NNP', 'N_NN', 'PSP', 'N_NN', 'V_VM', 'JJ', 'V_VM', 'V_VAUX', 'RD_PUNC'], ['N_NNP', 'PSP', 'N_NN', 'PSP', 'N_NN', 'N_NN', 'N_NNP', 'PSP', 'N_NN', 'V_VM', 'V_VAUX', 'CC_CCD', 'PR_PRP', 'N_NNP', 'PSP', 'N_NN', 'JJ', 'V_VM', 'RD_PUNC'], ['CC_CCS', 'RB', 'JJ', 'N_NN', 'PSP', 'N_NNP', 'N_N

In [118]:
label_tokenizer = Tokenizer()
label_tokenizer.fit_on_texts(pos_label_dis)
label_index = label_tokenizer.word_index
train_label_sequences = label_tokenizer.texts_to_sequences(pos_label_dis)
padded_label_sequence = pad_sequences(train_label_sequences,padding="post",maxlen=52,truncating="post")
print(padded_label_sequence)


[[ 7  1  0 ...  0  0  0]
 [ 1  2  7 ...  0  0  0]
 [22  7  7 ...  0  0  0]
 ...
 [ 7 13  1 ...  0  0  0]
 [10 13 17 ...  0  0  0]
 [ 1  2  6 ...  0  0  0]]


In [58]:
print(len(word_index))
print(len(char_index))
print(len(padded_word_sequences_dis[0]))
print(char_index)
print(word_index)

4987
125
52
{'<OOV>': 1, 'ा': 2, 'क': 3, 'र': 4, 'े': 5, '्': 6, 'ि': 7, 'स': 8, 'त': 9, 'ं': 10, 'ी': 11, 'न': 12, 'ह': 13, 'ो': 14, 'म': 15, 'य': 16, 'प': 17, 'ल': 18, 'व': 19, 'ै': 20, 'ज': 21, 'द': 22, 'ग': 23, 'ब': 24, 'ु': 25, '।': 26, 'च': 27, 'ट': 28, ',': 29, 'श': 30, 'अ': 31, 'ू': 32, 'थ': 33, 'ए': 34, 'भ': 35, 'इ': 36, 'ध': 37, 'ड': 38, 'ण': 39, 'ष': 40, 'उ': 41, 'फ': 42, 'औ': 43, 'आ': 44, 'l': 45, 'ख': 46, '़': 47, '"': 48, '0': 49, 'n': 50, '(': 51, ')': 52, '1': 53, 'u': 54, 'ई': 55, 'छ': 56, 'ओ': 57, '-': 58, 'e': 59, '2': 60, 'i': 61, 'ृ': 62, 'o': 63, 'ौ': 64, 'a': 65, 'ॉ': 66, 'r': 67, 's': 68, '9': 69, 't': 70, 'h': 71, '5': 72, 'घ': 73, 'm': 74, 'p': 75, 'ठ': 76, '6': 77, 'ँ': 78, 'ऐ': 79, '.': 80, '4': 81, 'ढ': 82, '8': 83, '०': 84, 'd': 85, 'c': 86, '3': 87, '7': 88, '%': 89, 'ः': 90, 'v': 91, ':': 92, 'ऑ': 93, 'ञ': 94, 'y': 95, '१': 96, 'झ': 97, '९': 98, 'f': 99, ';': 100, 'b': 101, 'g': 102, 'z': 103, 'j': 104, 'k': 105, '/': 106, 'ऊ': 107, 'w': 108, '५': 109, "

In [0]:
def pretrained_embedding_layer(word_to_vec_map1,word_to_vec_map2,word_to_index):
  vocab_len = len(word_to_index) + 1
  # emb_dim1 = word_to_vec_map1["और"].shape[0]
  # emb_dim2 = word_to_vec_map2["और"].shape[0]
  emb_matrix = np.zeros((vocab_len,100))
  
  # for word, idx in word_to_index.items():
  #     emb_matrix[idx, :] = np.concatenate((word_to_vec_map1[word].T,word_to_vec_map2[word].T),axis=1)

  embedding_layer = Embedding(vocab_len,100,input_length=52)
  # embedding_layer.trainable = True
  # embedding_layer.build((vocab_len,))
  # embedding_layer.set_weights([emb_matrix])
#from gensim.models import Word2Vec
# word_to_vec = Word2Vec(pos_feature_dis, size=100, window=5, min_count=5, workers=4, sg=0)
# from gensim.models import FastText
# fasttext = FastText(pos_feature_dis, size=100, window=5, min_count=5, workers=4,sg=1)



# #glove implementation

# from glove import Corpus, Glove

# corpus = Corpus() 

# corpus.fit(pos_feature_dis, window=10)
# #creating a Glove object which will use the matrix created in the above lines to create embeddings
# #We can set the learning rate as it uses Gradient Descent and number of components
# glove = Glove(no_components=5, learning_rate=0.05)
 
# glove.fit(corpus.matrix, epochs=30, no_threads=4, verbose=True)
# glove.add_dictionary(corpus.dictionary)
# glove.save('glove.model')
# print(glove.word_vectors[glove.dictionary['था']])trix])
  
  return embedding_layer

In [0]:
from tensorflow.keras.layers import Flatten
import numpy as np
from tensorflow.keras.models import Model

In [0]:
def charcnn(char_index,block):
    vocab_size = len(char_index)+1
    conv_layers = [[64,3,3],
                   [128,3,-1]]
    dropout_p = 0.3
    num_of_classes = 16
    embedding_size = 30

    fully_connected_layers = [128, 64]
    #print(block)
   # char_sequence = char_vectorizer.texts_to_sequences(block)
  #  char_padded_sequence = pad_sequences(char_sequences,maxlen=CHAR_MAX_LENGTH,padding='post',truncating='post')           
    
    embedding_layer = Embedding(vocab_size,embedding_size,input_length=CHAR_MAX_LENGTH)
    x = embedding_layer(block)
    for filter_num, filter_size, pooling_size in conv_layers:
        x = Conv1D(filter_num, filter_size)(x)
        x = Activation('relu')(x)
        if pooling_size != -1:
            x = MaxPooling1D(pool_size=pooling_size)(x)  
    x = Flatten()(x)
    for dense_size in fully_connected_layers:
        x = Dense(dense_size, activation='relu')(x)  
        x = Dropout(dropout_p)(x)
    # Output Layer
    predictions = Dense(num_of_classes, activation='relu')(x)
    return predictions

In [0]:
def CrossDomain(word_to_vec_map, word_to_vec_map1, word_to_index):
  input_shape = (52,)
  input_shape1 = (52,CHAR_MAX_LENGTH)

  sentence_indices = Input(shape=input_shape,dtype='int32')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  sentence_word = Input(shape=input_shape1)
  char_feat = []
  for t in range(52):
    sentence_word_x = Lambda(lambda x : x[:,t,:])(sentence_word)
#    sentence_word_x = Reshape((1,))(sentence_word_x)
    char_feat.append(charcnn(char_index,sentence_word_x))
  print(len(char_feat))
  print(char_feat[0].shape)
  print(embeddings.shape)
  char_feat_tensor = tf.stack(char_feat,axis=1)
  print(char_feat_tensor.shape)
  
  mixed_embeddings = Concatenate()([embeddings,char_feat_tensor])

  print(mixed_embeddings.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)
  print(X.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  print(X.shape)
  X = Dropout(rate=0.5)(X)
  print(X.shape)
  X = Dense(units=40)(X)
  X = Activation('softmax')(X)
  print(X.shape)
  model = Model(inputs=[sentence_indices,sentence_word],outputs=X)
  return model

In [131]:
from tensorflow.keras.optimizers import Adam
opt = Adam(lr=0.01, beta_1=0.9, beta_2=0.999, decay=0.01)
model = CrossDomain({},{},word_index)
model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy']) 

52
(?, 16)
(?, 52, 100)
(?, 52, 16)
(?, 52, 116)
(?, 52, 256)
(?, 52, 256)
(?, 52, 256)
(?, 52, 256)
(?, 52, 256)
(?, 52, 40)


In [132]:
print(len(label_index))
print(label_index)
print(padded_label_sequence[0])

39
{'n_nn': 1, 'psp': 2, 'v_vm': 3, 'v_vaux': 4, 'rd_punc': 5, 'jj': 6, 'n_nnp': 7, 'cc_ccd': 8, 'rd_sym': 9, 'pr_prp': 10, 'qt_qtc': 11, 'qt_qtf': 12, 'rp_rpd': 13, 'n_nst': 14, 'pr_prl': 15, 'rd_rdf': 16, 'cc_ccs': 17, 'dm_dmd': 18, 'rb': 19, 'rp_neg': 20, 'rp_intf': 21, 'qt_qto': 22, 'dm_dmi': 23, 'pr_prf': 24, 'rd_unk': 25, 'dm_dmr': 26, 'null': 27, 'pr_pri': 28, 'pr_prq': 29, 'dm_dmq': 30, 'nnp': 31, 'dm__dmd': 32, 'nn': 33, 'intf': 34, 'rd_ech': 35, 'rp__rpd': 36, 'v__vm': 37, 'cc': 38, 'rp_inj': 39}
[7 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0]


In [133]:
model.summary()

Model: "model_10"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_59 (InputLayer)           [(None, 52, 22)]     0                                            
__________________________________________________________________________________________________
lambda_1049 (Lambda)            (None, 22)           0           input_59[0][0]                   
__________________________________________________________________________________________________
lambda_1050 (Lambda)            (None, 22)           0           input_59[0][0]                   
__________________________________________________________________________________________________
lambda_1051 (Lambda)            (None, 22)           0           input_59[0][0]                   
___________________________________________________________________________________________

In [0]:
def CrossTask(word_to_vec_map,word_to_vec_map1, word_to_index):
  
  input_shape = (52,)
  input_shape1 = (52,CHAR_MAX_LENGTH)

  sentence_indices = Input(shape=input_shape,dtype='int32')
  embedding_layer = pretrained_embedding_layer(word_to_vec_map,word_to_vec_map1 ,word_to_index)
  embeddings = embedding_layer(sentence_indices)

  sentence_word = Input(shape=input_shape1)
  char_feat = []
  for t in range(52):
    sentence_word_x = Lambda(lambda x : x[:,t,:])(sentence_word)
#    sentence_word_x = Reshape((1,))(sentence_word_x)
    char_feat.append(charcnn(char_index,sentence_word_x))
  print(len(char_feat))
  print(char_feat[0].shape)
  print(embeddings.shape)
  char_feat_tensor = tf.stack(char_feat,axis=1)
  print(char_feat_tensor.shape)
  
  mixed_embeddings = Concatenate()([embeddings,char_feat_tensor])



  X = Bidirectional(GRU(units=128,return_sequences=True))(mixed_embeddings)
  X = Bidirectional(GRU(units=128,return_sequences=True))(X)
  X1 = Dropout(rate=0.5)(X)
  X1 = Bidirectional(GRU(units=128,return_sequences=True))(X1)
  X1 = Dropout(rate=0.5)(X1)
  X1 = Dense(units=40)(X1)
  X1 = Activation('softmax')(X1)
  X2 = Dropout(rate=0.5)(X)
  X2 = Bidirectional(GRU(units=128,return_sequences=True))(X2)
  X2 = Dropout(rate=0.5)(X2)
  X2 = Dense(units=8)(X2)
  X2 = Activation('softmax')(X2)
  model = Model(inputs=[sentence_indices,sentence_word],outputs=[X1,X2])
  return model

In [144]:
from tensorflow.keras.optimizers import Adam
opt = Adam(lr=0.01, beta_1=0.9, beta_2=0.999, decay=0.01)
model = CrossTask({},{},word_index)
model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=['accuracy']) 

52
(?, 16)
(?, 52, 100)
(?, 52, 16)


In [145]:
model.summary()

Model: "model_13"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_65 (InputLayer)           [(None, 52, 22)]     0                                            
__________________________________________________________________________________________________
lambda_1205 (Lambda)            (None, 22)           0           input_65[0][0]                   
__________________________________________________________________________________________________
lambda_1206 (Lambda)            (None, 22)           0           input_65[0][0]                   
__________________________________________________________________________________________________
lambda_1207 (Lambda)            (None, 22)           0           input_65[0][0]                   
___________________________________________________________________________________________